In [ ]:
%%capture
!pip install gdown
!pip install TTS
!sudo apt-get install espeak-ng -y
!sudo apt-get install unzip
!gdown "https://drive.google.com/uc?id=your_id"
!unzip /teamspace/studios/this_studio/data.zip -d /teamspace/studios/this_studio/data

In [ ]:
from huggingface_hub import snapshot_download
local_data_dir = "/teamspace/studios/this_studio/model/male_vits_23_dec_2024-December-23-2024_09+14AM-0000000"
dataset_repo = "sifat1221/vits_bn_tts_checkpoint_45000"
file_path = snapshot_download(repo_id=dataset_repo, local_dir=local_data_dir)

In [1]:
import os
folder_path = "/teamspace/studios/this_studio/data/data/wav"
file_count = len([f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))])
print(f"Number of files in '{folder_path}': {file_count}")

Number of files in '/teamspace/studios/this_studio/data/data/wav': 17670


In [2]:
import numpy as np
import pandas as pd
import os
# os.environ["CUDA_VISIBLE_DEVICES"] = "0"
import torch
from trainer import Trainer, TrainerArgs
from TTS.tts.configs.shared_configs import BaseDatasetConfig
from TTS.tts.configs.vits_config import VitsConfig
from TTS.utils.audio import AudioProcessor
from TTS.tts.datasets import load_tts_samples
from TTS.tts.utils.text.tokenizer import TTSTokenizer
from TTS.tts.models.vits import Vits, VitsAudioConfig, CharactersConfig

In [3]:
if "COLAB_GPU" in os.environ:
    from google.colab import drive
    drive.mount('/content/drive')
    data_root = '/content/drive/MyDrive/IIT/4-2/ML/ML-Project_Team_minions/data'
    model_root = '/content/drive/MyDrive/IIT/4-2/ML/ML-Project_Team_minions/Models'
    
elif os.path.exists("/kaggle"):
    print("Running in Kaggle")
    data_root = '/kaggle/input/bangla-audio/data'
    model_root = '/kaggle/working/'

else:
    print("Running in Lightening")
    data_root = '/teamspace/studios/this_studio/data/data'
    model_root = '/teamspace/studios/this_studio/model'


Running in Lightening


In [4]:
male = True
pretrained = True
pretrained_path = ""
if(pretrained):
    pretrained_path = '/teamspace/studios/this_studio/model/male_vits_23_dec_2024-December-23-2024_09+14AM-0000000'
    
if(male):
    meta_file = f'{data_root}/metadata.csv'
    root_path = f'{data_root}'
else:
    meta_file = f'{data_root}/female/mono/metadata_female.txt'
    root_path = f'{data_root}/female/mono'

In [5]:
def formatter(root_path, meta_file, **kwargs):  # pylint: disable=unused-argument
    txt_file = meta_file
    items = []
    speaker_name = "ljspeech"
    with open(txt_file, "r", encoding="utf-8") as ttf:
        for line in ttf:
            cols = line.split("|")
            wav_file = os.path.join(root_path, "wav", cols[0] + ".wav")
            print("wav_file:",wav_file)
            text = ''
            try:
                text = cols[2]
                print("text:",text)
            except:
                print("not found")
            items.append({"text": text, "audio_file": wav_file, "speaker_name": speaker_name, "root_path": root_path})
    return items

In [6]:
dataset_config = BaseDatasetConfig(meta_file_train=meta_file, path=os.path.join(root_path, ""))

train_samples, eval_samples = load_tts_samples(dataset_config,formatter=formatter, eval_split=True, eval_split_size=0.2)
# print(help(load_tts_samples))

print(len(train_samples),len(eval_samples))

wav_file: /teamspace/studios/this_studio/data/data/wav/01001.wav
text: উনিশ মে দুপুর তিনটায় হোটেল সুন্দরবনে আপনার একটি রিজার্ভেশন আছে।

wav_file: /teamspace/studios/this_studio/data/data/wav/01002.wav
text: শেখ হাসিনা বাংলাদেশ আওয়ামী লীগের সভানেত্রী।

wav_file: /teamspace/studios/this_studio/data/data/wav/01003.wav
text: আপনার বাড়ি এবং আপনার কাজের জায়গার মধ্যে ট্রাফিক দেখানো হচ্ছে ।

wav_file: /teamspace/studios/this_studio/data/data/wav/01004.wav
text: জাহানারা ইমামের জন্ম উনিশ শত উনত্রিশ সালের তিন মে বর্তমান পশ্চিমবঙ্গের মুর্শিদাবাদ জেলায়।

wav_file: /teamspace/studios/this_studio/data/data/wav/01005.wav
text: এইগুলো সিক্স ফ্ল্যাগস এর কয়েকটি রাইড।

wav_file: /teamspace/studios/this_studio/data/data/wav/01006.wav
text: আপনি শেষ হবার সময় বলতে পারেন উদাহরণস্বরূপ ছয় পি এম।

wav_file: /teamspace/studios/this_studio/data/data/wav/01007.wav
text: মুহম্মদ জাফর ইকবাল একজন বাংলাদেশী লেখক, পদার্থবিদ ও শিক্ষাবিদ।

wav_file: /teamspace/studios/this_studio/data/data/wav/01008.wav
text: এই 

In [7]:
output_path = model_root
phoneme_cache_path = os.path.join(output_path, "phoneme_cache")
os.makedirs(output_path,exist_ok=True)


audio_config = VitsAudioConfig(sample_rate=22050, win_length=1024, hop_length=256, num_mels=80, mel_fmin=0, mel_fmax=None)
config = VitsConfig(
    audio=audio_config,
    run_name="male_vits_23_dec_2024",
    batch_size=48,
    eval_batch_size=32,
    epochs=1000,
    save_step=5000,
    print_step=500,
    batch_group_size=0,
    num_loader_workers=8,
    num_eval_loader_workers=8,
    run_eval=True,
    test_delay_epochs=-1,
    phonemizer="espeak",
    text_cleaner='phoneme_cleaners', #'multilingual_cleaners', #"collapse_whitespace" phoneme_cleaners multilingual_cleaners
    use_phonemes=True,
    phoneme_language="bn",
    phoneme_cache_path=phoneme_cache_path,
    compute_input_seq_cache=True,
    add_blank=True,
    use_language_weighted_sampler = True,
    print_eval=False,
    mixed_precision=False,
    output_path=output_path,
    datasets=[dataset_config],
    # characters = characters_config,
    cudnn_benchmark=True,
    test_sentences = [
        'আমার   সোনার বাংলা, আমি তোমায় ভালোবাসি।',
        'চিরদিন   তোমার আকাশ, তোমার বাতাস, আমার প্রাণে বাজায় বাঁশি',
        'ও মা,   ফাগুনে তোর আমের বনে ঘ্রাণে পাগল করে,মরি হায়, হায় রে।'
    ]
)

ap = AudioProcessor.init_from_config(config)
tokenizer, config = TTSTokenizer.init_from_config(config)
model = Vits(config, ap, tokenizer, speaker_manager=None)
trainer = Trainer(TrainerArgs(continue_path = pretrained_path), config, output_path, model=model, train_samples=train_samples, eval_samples=eval_samples)

 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024


fatal: not a git repository (or any parent up to mount point /teamspace/studios)
Stopping at filesystem boundary (GIT_DISCOVERY_ACROSS_FILESYSTEM not set).
 > Training Environment:
 | > Backend: Torch
 | > Mixed precision: False
 | > Precision: float32
 | > Current device: 0
 | > Num. of GPUs: 1
 | > Num. of CPUs: 16
 | > Num. of Torch Threads: 8
 | > Torch seed: 54321
 | > Torch CUDNN: True
 | > Torch CUDNN deterministic: False
 | > Torch CUDNN benchmark: True
 | > Torch TF32 MatMul: False
 > Start Tensorboard: tensorboard --logdir=/teamspace/studios/this_studio/model/male_vits_23_dec_2024-December-23-2024_09+14AM-0000000
 > Restoring from best_model_17967.pth ...
/home/zeus/miniconda3/envs/cloudspace/lib/python3.10/site-packages/trainer/io.py:76: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpi

In [8]:
%%time
trainer.fit()

 > Restoring best loss from best_model_17967.pth ...
 > Starting with loaded last best loss {'train_loss': 15.75434464175685, 'eval_loss': 15.74705525745045}

 > EPOCH: 0/1000
 --> /teamspace/studios/this_studio/model/male_vits_23_dec_2024-December-23-2024_09+14AM-0000000


[*] Pre-computing phonemes...


  0%|          | 8/14136 [00:00<03:10, 74.18it/s]

ˌei nˈiɾbatʃˌɔn ˈupɔɟˌela bˈa ɟˈela bʰˈittik hˈɔbe
 [!] Character 'ʰ' not found in the vocabulary. Discarding it.


  0%|          | 23/14136 [00:00<04:23, 53.58it/s]

...

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.009152882749384098 (+0.00024818723851983623)
     | > avg_loss_disc: 2.554439969496293 (-0.10130776275288023)
     | > avg_loss_disc_real_0: 0.13072747716849498 (+0.015756751258264853)
     | > avg_loss_disc_real_1: 0.22366285053166476 (-0.0739025441083043)
     | > avg_loss_disc_real_2: 0.25848272727294397 (-0.02876459996808678)
     | > avg_loss_disc_real_3: 0.23065950667316262 (-0.003956314785913989)
     | > avg_loss_disc_real_4: 0.2770507858558136 (+0.03457522717389208)
     | > avg_loss_disc_real_5: 0.2414113399657336 (+0.027479489960453712)
     | > avg_loss_0: 2.554439969496293 (-0.10130776275288023)
     | > avg_loss_gen: 2.13484359221025 (+0.13768897490067933)
     | > avg_loss_kl: 1.839314650405537 (+0.021093117107044757)
     | > avg_loss_feat: 4.856792389262806 (+0.3342688928950919)
     | > avg_loss_mel: 19.161781744523495 (-0.18015899658202628)
     | > avg_loss_duration: 1.5938009489666332 (-0.019432205503637112)
     

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.009078784422440962 (-7.409832694313563e-05)
     | > avg_loss_disc: 2.6593308058652 (+0.10489083636890717)
     | > avg_loss_disc_real_0: 0.1970122777602889 (+0.06628480059179392)
     | > avg_loss_disc_real_1: 0.27639342424544416 (+0.0527305737137794)
     | > avg_loss_disc_real_2: 0.26927172216502104 (+0.010788994892077075)
     | > avg_loss_disc_real_3: 0.2553422804583203 (+0.02468277378515768)
     | > avg_loss_disc_real_4: 0.25493231361562574 (-0.02211847224018787)
     | > avg_loss_disc_real_5: 0.2529537733305583 (+0.011542433364824689)
     | > avg_loss_0: 2.6593308058652 (+0.10489083636890717)
     | > avg_loss_gen: 2.161815135045483 (+0.026971542835232842)
     | > avg_loss_kl: 1.8596554084257646 (+0.0203407580202275)
     | > avg_loss_feat: 4.526265018636529 (-0.33052737062627724)
     | > avg_loss_mel: 19.26052365736528 (+0.0987419128417848)
     | > avg_loss_duration: 1.597612391818653 (+0.003811442852019953)
     | > avg_

: 

In [1]:
from huggingface_hub import HfApi, upload_folder

api_token = "your_token"
repo_id = "sifat1221/vits_bn_tts_checkpoint_25000"
local_dir = '/teamspace/studios/this_studio/model/male_vits_23_dec_2024-December-23-2024_09+14AM-0000000'

api = HfApi(token=api_token)
api.create_repo(repo_id=repo_id, repo_type="model", private=False, exist_ok=True)

upload_folder(
    folder_path=local_dir,
    path_in_repo="",
    repo_id=repo_id,
    token=api_token,
    repo_type="model",
)
print(f"Files from '{local_dir}' uploaded to the repository '{repo_id}' successfully.")

best_model_19443.pth:   0%|          | 0.00/998M [00:00<?, ?B/s]

checkpoint_25000.pth:   0%|          | 0.00/998M [00:00<?, ?B/s]

checkpoint_20000.pth:   0%|          | 0.00/998M [00:00<?, ?B/s]

Upload 13 LFS files:   0%|          | 0/13 [00:00<?, ?it/s]

best_model_19443.pth:   0%|          | 0.00/998M [00:00<?, ?B/s]

...

events.out.tfevents.1734986943.ip-10-192-12-170.29923.0:   0%|          | 0.00/12.6k [00:00<?, ?B/s]

events.out.tfevents.1735012004.ip-10-192-12-114.1960.0:   0%|          | 0.00/14.7M [00:00<?, ?B/s]

events.out.tfevents.1735020584.ip-10-192-12-126.2401.0:   0%|          | 0.00/9.24k [00:00<?, ?B/s]

events.out.tfevents.1735020769.ip-10-192-12-115.2921.0:   0%|          | 0.00/25.8M [00:00<?, ?B/s]

Files from '/teamspace/studios/this_studio/model/male_vits_23_dec_2024-December-23-2024_09+14AM-0000000' uploaded to the repository 'sifat1221/vits_bn_tts_checkpoint_25000' successfully.
